## RNN


### Installation of packages


In [376]:
%pip install torch
%pip install torchtext
%pip install datasets
%pip install pandas
%pip install scikit-learn

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


### Importing libraries


In [377]:
from collections import Counter
import torch
import pandas as pd
from torchtext.vocab import vocab
from sklearn.model_selection import train_test_split
from tqdm.notebook import tqdm

### Read datasets


In [378]:
def read_data():
    train_dataset = pd.read_csv(
        "train/train.tsv.xz", compression="xz", sep="\t", names=["Label", "Text"]
    )
    dev_0_dataset = pd.read_csv("dev-0/in.tsv", sep="\t", names=["Text"])
    dev_0_labels = pd.read_csv("dev-0/expected.tsv", sep="\t", names=["Label"])
    test_A_dataset = pd.read_csv("test-A/in.tsv", sep="\t", names=["Text"])

    return train_dataset, dev_0_dataset, dev_0_labels, test_A_dataset

In [379]:
train_dataset, dev_0_dataset, dev_0_labels, test_A_dataset = read_data()

### Split the training data into training and validation sets


In [380]:
train_texts, val_texts, train_labels, val_labels = train_test_split(
    train_dataset["Text"], train_dataset["Label"], test_size=0.1, random_state=42
)

In [381]:
train_dataset = pd.DataFrame({"Text": train_texts, "Label": train_labels})
val_dataset = pd.DataFrame({"Text": val_texts, "Label": val_labels})

### Tokenize the text and labels


In [382]:
train_dataset["tokenized_text"] = train_dataset["Text"].apply(lambda x: x.split())
train_dataset["tokenized_labels"] = train_dataset["Label"].apply(lambda x: x.split())

In [383]:
val_dataset["tokenized_text"] = val_dataset["Text"].apply(lambda x: x.split())
val_dataset["tokenized_labels"] = val_dataset["Label"].apply(lambda x: x.split())

In [384]:
dev_0_dataset["tokenized_text"] = dev_0_dataset["Text"].apply(lambda x: x.split())
dev_0_dataset["tokenized_labels"] = dev_0_labels["Label"].apply(lambda x: x.split())

In [385]:
test_A_dataset["tokenized_text"] = test_A_dataset["Text"].apply(lambda x: x.split())

### Create a vocab object which maps tokens to indices


In [386]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [387]:
v = build_vocab(train_dataset["tokenized_text"])

### Map indices to tokens


In [388]:
itos = v.get_itos()

### Number of tokens in the vocabulary


In [389]:
len(itos)

22154

### Index of the 'rejects' token


In [390]:
v["rejects"]

9086

### Index of the '\<unk\>' token


In [391]:
v["<unk>"]

0

### Set the default index to the unknown token


In [392]:
v.set_default_index(v["<unk>"])

### Use cuda if available


In [393]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

### Vectorize the data


In [394]:
def data_process(dt):
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in document] + [v["<eos>"]],
            dtype=torch.long,
            device=device,
        )
        for document in dt
    ]

In [395]:
train_tokens_ids = data_process(train_dataset["tokenized_text"])
val_tokens_ids = data_process(val_dataset["tokenized_text"])
dev_0_tokens_ids = data_process(dev_0_dataset["tokenized_text"])
test_A_tokens_ids = data_process(test_A_dataset["tokenized_text"])

### Create a mapping from label to index


In [396]:
labels = ["O", "B-PER", "I-PER", "B-ORG", "I-ORG", "B-LOC", "I-LOC", "B-MISC", "I-MISC"]

label_to_index = {label: idx for idx, label in enumerate(labels)}

### Vectorize the labels (NER)


In [397]:
def labels_process(dt, label_to_index):
    return [
        torch.tensor(
            [0] + [label_to_index[label] for label in document] + [0],
            dtype=torch.long,
            device=device,
        )
        for document in dt
    ]

In [398]:
train_labels = labels_process(train_dataset["tokenized_labels"], label_to_index)
val_labels = labels_process(val_dataset["tokenized_labels"], label_to_index)
dev_0_labels = labels_process(dev_0_dataset["tokenized_labels"], label_to_index)

### Function for evaluation (returns precision, recall, and F1 score)


In [399]:
def get_scores(y_true, y_pred):
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0

    for p, t in zip(y_pred, y_true):
        if p == t:
            acc_score += 1

        if p > 0 and p == t:
            tp += 1

        if p > 0:
            selected_items += 1

        if t > 0:
            relevant_items += 1

    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items

    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items

    if precision + recall == 0.0:
        f1 = 0.0
    else:
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1

### Calculate the number of unique tags


In [400]:
all_label_indices = [
    label_to_index[label]
    for document in train_dataset["tokenized_labels"]
    for label in document
]

num_tags = max(all_label_indices) + 1

print(num_tags)

9


### Implementation of a recurrent neural network LSTM


In [401]:
class LSTM(torch.nn.Module):

    def __init__(self, vocab_size, embedding_dim, hidden_dim, num_layers, num_tags):
        super(LSTM, self).__init__()
        self.embedding = torch.nn.Embedding(vocab_size, embedding_dim)
        self.rec = torch.nn.LSTM(
            embedding_dim, hidden_dim, num_layers, batch_first=True, bidirectional=True
        )
        self.fc1 = torch.nn.Linear(hidden_dim * 2, num_tags)

    def forward(self, x):
        embedding = torch.relu(self.embedding(x))
        lstm_output, _ = self.rec(embedding)
        out_weights = self.fc1(lstm_output)
        return out_weights

### Initialize the LSTM model


In [402]:
lstm = LSTM(len(v.get_itos()), 100, 100, 1, num_tags).to(device)

### Define the loss function


In [403]:
criterion = torch.nn.CrossEntropyLoss()

### Define the optimizer


In [404]:
optimizer = torch.optim.Adam(lstm.parameters())

### Function for model evaluation


In [405]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        tags = list(dataset_labels[i].cpu().numpy())
        Y_true += tags

        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred += list(Y_batch_pred.cpu().numpy())

    return get_scores(Y_true, Y_pred)

### Function for returning the predictions labels


In [406]:
def pred_labels(dataset_tokens, model, label_to_index):
    Y_pred = []
    inv_label_to_index = {
        v: k for k, v in label_to_index.items()
    }  # Create the inverse mapping

    dataset_tokens = dataset_tokens[1:-1]

    for i in tqdm(range(len(dataset_tokens))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        predicted_labels = [inv_label_to_index[label.item()] for label in Y_batch_pred]
        Y_pred.append(" ".join(predicted_labels))

    return Y_pred

### Training


In [407]:
NUM_EPOCHS = 20

In [408]:
for i in range(NUM_EPOCHS):
    lstm.train()
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0)
        tags = train_labels[i].unsqueeze(1)

        predicted_tags = lstm(batch_tokens)

        optimizer.zero_grad()
        loss = criterion(predicted_tags.squeeze(0), tags.squeeze(1))

        loss.backward()
        optimizer.step()

    lstm.eval()
    print(eval_model(val_tokens_ids, val_labels, lstm))

  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

(0.7132680320569902, 0.23037100949094047, 0.3482608695652174)


  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

...

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8432908912830558, 0.7428817946505608, 0.789908256880734)


  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8448275862068966, 0.7469082542421628, 0.7928560525110669)


In [409]:
eval_model(val_tokens_ids, val_labels, lstm)

  0%|          | 0/95 [00:00<?, ?it/s]

(0.8448275862068966, 0.7469082542421628, 0.7928560525110669)

In [410]:
eval_model(dev_0_tokens_ids, dev_0_labels, lstm)

  0%|          | 0/215 [00:00<?, ?it/s]

(0.871974921630094, 0.8103006292239571, 0.8400072476897988)

In [411]:
dev_0_predictons = pred_labels(dev_0_tokens_ids, lstm, label_to_index)
dev_0_predictons = pd.DataFrame(dev_0_predictons, columns=["Label"])
dev_0_predictons.to_csv("dev-0/out.tsv", index=False, header=False)

  0%|          | 0/213 [00:00<?, ?it/s]

In [412]:
test_A_predictions = pred_labels(test_A_tokens_ids, lstm, label_to_index)
test_A_predictions = pd.DataFrame(test_A_predictions, columns=["Label"])
test_A_predictions.to_csv("test-A/out.tsv", index=False, header=False)

  0%|          | 0/228 [00:00<?, ?it/s]